In [ ]:
import numpy as np
import random
from scipy.spatial import distance
from sklearn.preprocessing import StandardScaler


#Store Data Variables
import json
with open('feature_data.json', 'r') as f:
 features = json.load(f)

from scipy.io import loadmat
train_idxs = loadmat('cuhk03_new_protocol_config_labeled.mat')['train_idx'].flatten()
query_idxs = loadmat('cuhk03_new_protocol_config_labeled.mat')['query_idx'].flatten()
labels = loadmat('cuhk03_new_protocol_config_labeled.mat')['labels'].flatten()
gallery_idxs = loadmat('cuhk03_new_protocol_config_labeled.mat')['gallery_idx'].flatten()
filelist = loadmat('cuhk03_new_protocol_config_labeled.mat')['filelist'].flatten()
camId = loadmat('cuhk03_new_protocol_config_labeled.mat')['camId'].flatten()

In [ ]:
train_idxs

In [ ]:
query_idxs

In [ ]:
labels

In [ ]:
gallery_idxs

In [ ]:
filelist

In [ ]:
camId

In [8]:
#grid searc cv against k, distance metric and transformation/normalization - use only query and gallery for this part 

In [9]:
#scaler = StandardScaler()
print(np.array(features))
#features = scaler.fit_transform(features)
X = np.array(features)
print(X)
y = np.array(labels)
filelist = np.array(filelist)
camId = np.array(camId)

[[0.13791114 1.12505555 0.05404324 ... 0.10747871 0.04081609 0.68009406]
 [0.02507781 0.9057585  0.00346441 ... 0.16763815 0.14764351 0.2700713 ]
 [0.09923808 1.09122825 0.01889733 ... 0.07981343 0.04958951 0.37923682]
 ...
 [0.50913167 2.1067946  1.12224829 ... 0.78767842 1.68007588 0.00259321]
 [0.44684452 1.87411916 1.51910186 ... 1.02090526 1.58616257 0.10876646]
 [0.46024311 2.31024432 1.20531154 ... 0.62753201 1.22394812 0.        ]]
[[0.13791114 1.12505555 0.05404324 ... 0.10747871 0.04081609 0.68009406]
 [0.02507781 0.9057585  0.00346441 ... 0.16763815 0.14764351 0.2700713 ]
 [0.09923808 1.09122825 0.01889733 ... 0.07981343 0.04958951 0.37923682]
 ...
 [0.50913167 2.1067946  1.12224829 ... 0.78767842 1.68007588 0.00259321]
 [0.44684452 1.87411916 1.51910186 ... 1.02090526 1.58616257 0.10876646]
 [0.46024311 2.31024432 1.20531154 ... 0.62753201 1.22394812 0.        ]]


In [10]:
mask_train = np.array(train_idxs).ravel()
mask_query = np.array(query_idxs).ravel()
mask_gallery = np.array(gallery_idxs).ravel()

mask_train = np.subtract(mask_train, 1)
mask_query = np.subtract(mask_query, 1)
mask_gallery = np.subtract(mask_gallery, 1)


X_train, X_query, X_gallery = X[mask_train, :], X[mask_query, :], X[mask_gallery, :]
y_train, y_query, y_gallery = y[mask_train], y[mask_query], y[mask_gallery]
filelist_train, filelist_query, filelist_gallery = filelist[mask_train], filelist[mask_query], filelist[mask_gallery]
camId_train, camId_query, camId_gallery = camId[mask_train], camId[mask_query], camId[mask_gallery]

In [11]:
len(X_train)

7368

In [12]:
len(set(y_train))

767

In [13]:
len(X_query)

1400

In [14]:
len(X_gallery)

5328

In [15]:
len(y_train)

7368

In [16]:
X_val = []
y_val = []
camId_val = []
val_ind = []
for i in range(7368):
        if(i not in val_ind):
            X_val.append(X_train[i])
            y_val.append(y_train[i])
            camId_val.append(camId_train[i])
            val_ind.append(i)
            for j in range(7368):
                if(y_train[i] == y_train[j] and i != j):
                    X_val.append(X_train[j])
                    y_val.append(y_train[j])
                    camId_val.append(camId_train[j])
                    val_ind.append(j)
            if ((len(set(y_val)) > 99)):
                break

In [17]:
X_val = np.array(X_val)
y_val = np.array(y_val)
camId_val = np.array(camId_val)

In [18]:
len((y_val))

966

In [19]:
len(X_val)

966

In [20]:
len(camId_val)

966

In [21]:
len(set(val_ind))

966

In [22]:
X_train_new = []
y_train_new = []
camId_train_new = []
for i in range(7368):
    if(i not in val_ind):
        X_train_new.append(X_train[i])
        y_train_new.append(y_train[i])
        camId_train_new.append(camId_train[i])

In [23]:
X_train_new = np.array(X_train_new)
y_train_new = np.array(y_train_new)
camId_train_new = np.array(camId_train_new)

In [24]:
len(X_train_new)

6402

In [25]:
len(y_train_new)

6402

In [26]:
len(camId_train_new)

6402

In [27]:
mask_vquery = np.random.choice(np.arange(966), 193, replace=False)
mask_vgallery = np.array(list(set(np.arange(0, 966)) - set(mask_vquery)))
print(type(mask_vquery[0]))
print(type(mask_vgallery[0]))
X_vquery, X_vgallery =  X_val[mask_vquery, :], X_val[mask_vgallery, :]
y_vquery, y_vgallery =  y_val[mask_vquery], y_val[mask_vgallery]
camId_vquery, camId_vgallery = camId_val[mask_vquery], camId_val[mask_vgallery]

<class 'numpy.int32'>
<class 'numpy.int32'>


In [28]:
len(X_vgallery)

773

In [29]:
import pandas as pd 
import numpy as np

from keras import layers, optimizers, regularizers
from keras.layers import Dense, Dropout, BatchNormalization, Activation
from keras.models import Sequential

from keras.utils import plot_model
#from kt_utils import *
import keras.backend as K

from sklearn import preprocessing, model_selection 
from keras.wrappers.scikit_learn import KerasRegressor

C:\Users\User\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [44]:
# create model
model = Sequential()
# layer 1
model.add(Dense(6144, input_dim=6144, activation='relu', kernel_initializer='normal'))
#layer 2
model.add(Dense(1024, activation='relu', kernel_initializer='normal'))
model.add(BatchNormalization())
model.add(Dropout(0.5))
#layer 3
model.add(Dense(128, activation='relu',kernel_initializer='normal'))
model.add(BatchNormalization())
model.add(Dropout(0.5))
#layer 4
model.add(Dense(2, activation='softmax'))
# Compile model
from keras import metrics
#optimizer = optimizers.SGD(lr=0.001, decay=1e-6, momentum=0.9, nesterov= False)
optimizer = optimizers.Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)
model.compile(optimizer = optimizer, loss='categorical_crossentropy') 

In [45]:
X_train_pairs = []
y_train_pair_lables = []
for Xtnn, ytnn, camId_t in zip(X_train_new, y_train_new, camId_train_new):
    for Xtnn2, ytnn2, camId_t2 in zip(X_train_new, y_train_new, camId_train_new):
        if ((camId_t == camId_t2) and (ytnn == ytnn2)):
            continue
        elif (ytnn == ytnn2):
            #for i in range (30):
            randindex = random.randint(0, 6401)
            Xtnn3 = X_train_new[randindex]
            ytnn3 = y_train_new[randindex]                 

            dist2 = 0
            if(ytnn == ytnn3):
                dist3 = 0
            else:
                dist3 = 1

            Xconcat = np.concatenate((Xtnn,Xtnn2,Xtnn3), axis = None)
            X_train_pairs.append(Xconcat)
            y_train_pair_lables.append((dist2,dist3))   

            Xconcat = np.concatenate((Xtnn,Xtnn3,Xtnn2), axis = None)
            X_train_pairs.append(Xconcat)
            y_train_pair_lables.append((dist3,dist2)) 

y_train_pair_lables = np.array(y_train_pair_lables)
X_train_pairs = np.array(X_train_pairs)
model.fit(X_train_pairs, y_train_pair_lables, batch_size = 150, epochs=5)

Epoch 1/5


ResourceExhaustedError: OOM when allocating tensor of shape [6144] and type float
	 [[node dense_21/Const (defined at C:\Users\User\Anaconda3\lib\site-packages\keras\backend\tensorflow_backend.py:430)  = Const[dtype=DT_FLOAT, value=Tensor<type: float shape: [6144] values: 0 0 0...>, _device="/job:localhost/replica:0/task:0/device:GPU:0"]()]]

Caused by op 'dense_21/Const', defined at:
  File "C:\Users\User\Anaconda3\lib\runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "C:\Users\User\Anaconda3\lib\runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "C:\Users\User\Anaconda3\lib\site-packages\ipykernel_launcher.py", line 16, in <module>
    app.launch_new_instance()
  File "C:\Users\User\Anaconda3\lib\site-packages\traitlets\config\application.py", line 658, in launch_instance
    app.start()
  File "C:\Users\User\Anaconda3\lib\site-packages\ipykernel\kernelapp.py", line 486, in start
    self.io_loop.start()
  File "C:\Users\User\Anaconda3\lib\

In [32]:
def get_acc_score(y_valid, y_q, tot_label_occur):
    recall = 0
    true_positives = 0
    
    k = 0
    
    max_rank = 30
    
    rank_A = np.zeros(max_rank)
    AP_arr = np.zeros(11)
    
    while (recall < 1) or (k < max_rank):
        if (y_valid[k] == y_q):
            
            true_positives = true_positives + 1
            recall = true_positives/tot_label_occur
            precision = true_positives/(k+1)
            
            AP_arr[round((recall-0.05)*10)] = precision
            
            for n in range (k, max_rank):
                rank_A[n] = 1
            
        k = k+1
        
    max_precision = 0
    for i in range(10, -1, -1):
        max_precision = max(max_precision, AP_arr[i])
        AP_arr[i] = max_precision
    
    AP_ = AP_arr.sum()/11
    
    return AP_, rank_A

In [33]:
rank_accuracies = []
AP = []

for val, camId_v, y_v  in zip(X_vquery, camId_vquery, y_vquery):
    v_v_dists = []
    y_valid = []
    for val2, camId_v2, y_v2  in zip(X_vgallery, camId_vgallery, y_vgallery):
        if ((camId_v == camId_v2) and (y_v == y_v2)):
            continue
        else:
            randindex = random.randint(0, 772)
            val3 = X_vgallery[randindex]
            y_v3 = y_vgallery[randindex]

            dist = model.predict(np.concatenate((val, val2, val3)).reshape((1,6144)))[0][0]
            print(dist)
            v_v_dists.append(dist)
            y_valid.append(y_v2)

    tot_label_occur = y_valid.count(y_v)
    v_v_dists = np.array(v_v_dists)
    y_valid = np.array(y_valid)

    
    _indexes = np.argsort(v_v_dists)

    # Sorted distances and labels
    v_v_dists, y_valid = v_v_dists[_indexes], y_valid[_indexes]
    print(v_v_dists)
    
    if tot_label_occur != 0:
        AP_, rank_A = get_acc_score(y_valid, y_v, tot_label_occur)

        AP.append(AP_)

        rank_accuracies.append(rank_A) 

    #if q  > 5:
    #    break
    #q = q+1

rank_accuracies = np.array(rank_accuracies)

total = rank_accuracies.shape[0]
rank_accuracies = rank_accuracies.sum(axis = 0)
rank_accuracies = np.divide(rank_accuracies, total)

i = 0
print ('Accuracies by Rank:')
while i < rank_accuracies.shape[0]:
    print('Rank ', i+1, ' = %.2f%%' % (rank_accuracies[i] * 100), '\t',
          'Rank ', i+2, ' = %.2f%%' % (rank_accuracies[i+1] * 100), '\t',
          'Rank ', i+3, ' = %.2f%%' % (rank_accuracies[i+2] * 100), '\t',
          'Rank ', i+4, ' = %.2f%%' % (rank_accuracies[i+3] * 100), '\t',
          'Rank ', i+5, ' = %.2f%%' % (rank_accuracies[i+4] * 100))
    i = i+5

AP = np.array(AP)

mAP = AP.sum()/AP.shape[0]
print('mAP = %.2f%%' % (mAP * 100))

0.9999932
0.9999989
0.9999981
0.99999917
0.99999344
0.9999987
0.99999964
0.9999999
0.92215234
0.9980464
0.9999951
0.999995
0.8816153
0.9999974
0.9999999
0.9847513
0.9988689
0.0008042744
0.999954
0.26236838
0.9999137
0.9998264
0.99784005
0.9999676
0.998379
0.9999362
0.9999831
0.9996313
0.0016908628
0.032044683
0.0032049215
0.88342446
0.99925226
0.99035865
0.0003548652
0.0026479093
0.99203813
0.001197948
0.00022708191
0.31743336
1.6881377e-05
6.737081e-06
0.029954191
0.8278785
3.970567e-07
0.981108
0.0005522536
0.075395495
0.14843144
0.9706207
0.990262
0.11859356
0.72617507
0.9945868
0.49036205
0.9998211
0.022213025
0.9999441
0.99890196
0.9999827
0.9995146
1.5312085e-05
5.392452e-05
0.9095526
0.07429117
0.24552669
0.95537335
0.62249035
0.99981433
0.8210462
0.09526633
0.5775276
0.9999939
0.9967603
0.71659935
0.99685705
0.5959623
0.013068368
0.98776567
0.97631377
0.002559872
0.99062246
0.99839455
0.99756765
0.99998665
0.99993885
0.9999987
0.95592076
0.99784434
0.012220381
0.011412908
0.206

0.96607834
0.9532791
0.0064057535
0.014409094
0.9974262
0.5300401
0.65722674
0.0018743951
0.99928814
0.7275329
0.9935854
0.014456525
0.9983382
0.5645701
0.98641586
0.9937262
0.6228398
0.8329523
[1.25906785e-11 1.87479121e-09 2.11691753e-09 4.05273077e-08
 4.91046848e-08 6.53588330e-08 3.01917936e-07 3.65490450e-07
 3.97056709e-07 5.32913475e-07 5.65345033e-07 5.90800767e-07
 7.84265410e-07 8.00067767e-07 8.83694440e-07 1.03501293e-06
 1.03990249e-06 1.66153677e-06 2.80229096e-06 2.80455288e-06
 4.12247118e-06 4.25240705e-06 5.59008686e-06 5.70106431e-06
 5.90895388e-06 6.73708109e-06 6.90793104e-06 7.39738334e-06
 9.90379067e-06 1.03466627e-05 1.08313197e-05 1.12804146e-05
 1.26946316e-05 1.53120855e-05 1.68813767e-05 1.77825532e-05
 1.92971529e-05 2.40520258e-05 2.51090642e-05 2.60502220e-05
 3.41097730e-05 3.68533365e-05 4.46243139e-05 4.71922758e-05
 4.85813835e-05 5.39245193e-05 5.87176110e-05 6.34027820e-05
 6.77413700e-05 6.94682240e-05 7.26832222e-05 7.95926608e-05
 1.14925271e-

0.52105755
0.75474936
0.9999087
0.0003332219
0.9999386
0.9607851
0.70957875
0.6801386
0.64023125
0.9996667
0.9993036
0.9665804
0.9999987
0.99416333
0.49821773
0.44391376
0.94701463
0.0011762494
0.998869
0.002071212
0.22762188
0.19456968
0.0070219547
0.14136171
0.7908147
0.9663932
0.00019877843
0.981687
0.19190395
0.9998952
0.027024789
0.97609055
0.9446554
0.98278815
0.99904627
0.35563436
0.9999336
0.0038679389
0.84110194
0.9966453
0.31475535
0.98761576
0.9990839
0.99968505
0.0004744111
0.99582773
0.305432
0.58074903
0.9995727
0.01587996
0.99863774
0.9342516
0.7467164
0.38776574
0.98238784
0.85323167
0.9990447
0.9089881
0.9817405
0.8387549
0.0026355467
0.0005843786
0.035631698
0.29855832
1.336489e-05
0.4443356
0.22164196
0.2687819
0.9406004
0.99670225
0.90802467
0.99785525
0.9990268
0.7739114
0.99964833
0.63497436
0.7507791
0.9996675
0.9999589
0.9996667
0.99949014
0.98482853
0.9919402
0.5937136
0.99612385
0.9989807
0.000764747
0.0013313168
0.029725533
1.7445299e-06
0.0009348761
0.105173

0.039741386
0.9999285
0.6231705
0.9288494
0.9995214
0.99996996
0.9999795
0.058946922
0.999962
0.9998305
0.9994684
[1.93043430e-08 7.99704907e-08 1.70584670e-07 1.82105282e-07
 3.61153809e-07 7.38968652e-07 7.66795324e-07 1.20513971e-06
 1.53155565e-06 1.72552996e-06 1.74452987e-06 2.72709417e-06
 2.79728215e-06 3.20327740e-06 3.22501592e-06 4.36767959e-06
 4.70754094e-06 4.91891433e-06 6.26583460e-06 6.83283224e-06
 8.88152044e-06 9.61453225e-06 1.33648900e-05 1.55384587e-05
 1.70127714e-05 1.72820291e-05 1.73829249e-05 1.79785111e-05
 1.80853349e-05 1.81081687e-05 1.96769233e-05 2.31288413e-05
 2.44406383e-05 2.71706085e-05 2.77702347e-05 2.89465279e-05
 3.57401332e-05 3.82073158e-05 3.94026974e-05 4.59914008e-05
 4.84654738e-05 5.45067778e-05 5.49775432e-05 6.03737863e-05
 6.11139549e-05 8.47297124e-05 9.49570822e-05 9.85961669e-05
 1.25612467e-04 1.32531160e-04 1.40343036e-04 1.43305646e-04
 1.44402991e-04 1.44737307e-04 1.53037035e-04 1.55541245e-04
 1.60163559e-04 1.67017555e-04 1

0.9875689
0.8602633
0.99872535
0.8867524
0.008883178
0.6720174
0.9999912
0.9734117
0.98568374
0.988357
0.9994747
0.9999889
0.99743634
0.079564236
0.075884774
0.017048601
0.12778975
0.027385972
0.30309355
0.97852737
0.9832634
0.9998809
0.9889579
0.8774581
0.9993081
0.9986557
0.98908603
0.9994117
0.17408451
0.98894763
0.992971
0.71899027
0.9967055
0.93771374
0.007333348
0.0034933996
0.00016736348
0.00015447028
0.0006585267
0.0040045683
0.07666569
0.013499984
0.99750406
4.819751e-05
0.0003501916
0.9999602
0.99923146
0.2632895
0.021931633
0.9996613
0.4814053
0.99687433
0.99999964
0.9996184
0.99993
0.8311023
0.18985806
0.99999917
0.9874636
0.418996
0.011107155
0.0011162183
0.0013110358
0.89204913
0.019141136
0.2440097
0.0006432869
0.08643479
0.01896846
0.06588287
0.9928087
0.85960513
0.045635823
0.8826349
0.9996537
0.99995196
0.36850223
0.3396981
0.00083705084
0.25373346
0.9999995
0.99246395
0.99998975
0.9999956
0.9998499
0.9993087
0.7980512
0.49134246
0.29798093
0.6583878
0.030547937
0.057

...

0.9722028
0.98744816
0.99749607
0.9953146
0.9982804
0.6613034
0.0012212971
0.59733224
0.00011474983
0.014353387
0.034254584
0.9999157
0.97096485
0.5497845
0.99961984
[6.40024256e-09 2.38636204e-07 2.93294761e-07 3.30299883e-07
 4.22694882e-07 1.32848720e-06 1.81086784e-06 2.65724566e-06
 4.29857937e-06 6.35067727e-06 6.59845819e-06 6.64127947e-06
 9.57460361e-06 1.27953308e-05 1.31900779e-05 1.99306523e-05
 2.11909282e-05 3.09536990e-05 3.15887009e-05 3.73542571e-05
 3.91195354e-05 4.58996547e-05 5.80793057e-05 7.35069625e-05
 7.76271045e-05 8.64863614e-05 9.04134067e-05 1.12505404e-04
 1.14749833e-04 1.26690036e-04 1.34224058e-04 1.40236138e-04
 1.67465812e-04 1.71765350e-04 1.88154256e-04 1.96914276e-04
 2.29200115e-04 2.55094492e-04 2.76045233e-04 3.09699157e-04
 3.10108386e-04 3.28947237e-04 3.67659464e-04 4.37549781e-04
 4.41783166e-04 4.45650221e-04 4.51790780e-04 4.62774682e-04
 4.67936043e-04 4.79902723e-04 5.52389945e-04 5.70600096e-04
 5.97710372e-04 6.30803173e-04 7.08288280

0.063358724
1.780936e-07
0.9826386
0.07213919
0.97639126
0.97718585
0.84981024
0.0010173329
0.03782357
5.839731e-05
0.004018491
0.015911296
0.6168698
0.0060913693
0.038762074
0.044127945
0.00040878967
0.00024540012
0.0005002293
0.0018811722
0.007501018
0.026798401
0.004827928
0.3947599
0.00061925943
0.01199559
0.069629245
0.45641962
0.99664587
0.7882552
0.24157274
0.0007631504
0.08031325
0.9983606
0.29120785
0.0018667139
0.9384948
0.4075156
0.0019436587
0.036176685
0.00085290015
0.4863928
0.3031952
0.09097251
0.19460969
0.04529538
0.12997864
6.037576e-06
0.106028035
0.24212517
0.63266903
0.99415624
0.2983396
0.37890917
0.0006223444
0.005010852
0.01610753
0.0017735511
0.7634412
0.8089098
0.765001
0.7723697
0.013180556
0.0003170665
0.15806697
0.0070816195
3.6161296e-11
0.011559239
0.12169016
0.5975178
0.00017040434
0.00501012
0.7153345
0.63954103
0.19642235
0.75167584
0.026699472
0.9928053
0.9999826
0.9969056
0.99255013
0.5765158
0.0010435455
0.09023379
0.013447157
0.16839556
0.000138639

0.36104268
0.57532203
0.010270822
0.9016654
0.009090095
0.017918738
8.863946e-06
0.000677061
0.0017675372
0.028899718
0.0004405697
0.31804767
0.085054584
0.59337837
0.20087682
0.0993881
0.9821009
0.97012883
0.9753777
0.98459136
0.00015581647
0.7490298
0.99886864
0.7731355
0.8530267
0.24600406
0.9589864
0.8155013
[3.61612962e-11 5.29348254e-09 2.24746461e-08 5.68961944e-08
 8.83595135e-08 1.78093600e-07 2.20169696e-07 3.45436689e-07
 4.80908966e-07 5.02886394e-07 8.76997262e-07 1.25181145e-06
 1.48216441e-06 1.71907971e-06 2.10158032e-06 2.20196694e-06
 3.43357419e-06 3.64849689e-06 3.72432987e-06 4.18322770e-06
 4.35386846e-06 5.06062497e-06 5.25916585e-06 6.03757599e-06
 6.46177432e-06 6.49693220e-06 7.88361376e-06 8.43562066e-06
 8.86394628e-06 9.48193610e-06 1.36569906e-05 1.38185660e-05
 1.67259532e-05 2.51271722e-05 2.96343096e-05 2.96723192e-05
 3.24149405e-05 3.28040296e-05 3.52732022e-05 3.82129983e-05
 3.85498861e-05 3.89375346e-05 4.00124081e-05 4.82492433e-05
 4.98527806e-05

0.075733766
0.9623732
0.9947249
0.24297406
0.5201898
0.9460282
0.9937057
0.9946067
0.039394356
0.13953088
0.2887153
0.001045116
0.22066091
0.029543644
0.98868227
0.34969705
0.23770729
0.0019791394
0.99916637
0.008688938
0.0036776774
0.000108395696
0.12875609
0.0028072335
2.1921924e-06
0.024170615
0.0009931717
0.2036187
6.007835e-05
0.06394679
0.0006456812
0.00017007435
9.701882e-07
0.26365748
0.002444753
0.00056746195
0.0010985123
0.78204656
0.004098014
0.0006152214
0.9245799
0.1849669
0.01383286
0.0113602355
0.23510775
0.22597845
0.003465195
0.06843404
0.011351238
0.3218619
0.6493207
0.6446332
0.052110855
1.0891688e-05
3.7143204e-06
0.0038416553
0.004216389
0.01964635
3.8840735e-05
0.52396744
0.037816145
0.0064965826
1.2993119e-05
0.00077925244
0.00017378922
0.00018685094
0.0063776113
0.006345352
0.00031361284
0.046779998
0.48364806
8.699262e-06
2.5651827e-08
0.00027969424
0.00014307053
8.95351e-06
5.6772045e-09
5.0790554e-06
0.0008738863
0.13466011
0.8486961
0.06760307
0.9976374
0.94

0.39302084
0.8828779
0.105860256
0.6786503
0.94772243
0.99572974
0.9999964
0.9998646
0.9999987
0.99971443
0.99735475
0.9999875
0.999995
0.0019586366
0.812464
0.115413986
0.0007236696
0.9999858
0.022901323
0.005279806
0.9981888
0.99998784
0.9999956
0.9997279
0.9989687
0.9999981
0.9999881
0.9948265
0.72135526
0.8960148
0.57584465
0.99981076
0.019065687
0.75277245
0.0014161672
0.0017954551
0.96998996
[7.07257808e-10 5.67720448e-09 6.11862694e-09 2.56518273e-08
 9.27458075e-08 3.56151276e-07 4.18426652e-07 9.70188239e-07
 1.00601369e-06 1.11484314e-06 1.16515093e-06 1.19433423e-06
 1.54000952e-06 1.95053371e-06 2.19219237e-06 3.65522897e-06
 3.71432043e-06 5.06410106e-06 5.07905543e-06 5.27393740e-06
 6.08425626e-06 7.39481584e-06 7.60804369e-06 8.69926225e-06
 8.95350968e-06 9.84349936e-06 9.85051520e-06 1.08916884e-05
 1.09008533e-05 1.18657026e-05 1.20146196e-05 1.23475320e-05
 1.29931186e-05 1.51862032e-05 1.71565389e-05 1.84004293e-05
 1.91276049e-05 2.70834007e-05 2.83728095e-05 2.85